In [88]:
import imageio
import numpy as np

from stable_baselines3 import PPO

model = PPO("MlpPolicy", "ALE/MsPacman-v5").learn(2_000_000)

images = []
obs = model.env.reset()
img = model.env.render(mode="rgb_array")
done = False
while done != True:
    images.append(img)
    action, _ = model.predict(obs)
    obs, _, done,_ = model.env.step(action)
    img = model.env.render(mode="rgb_array")

imageio.mimsave("MsPacman_DQN.gif", [np.array(img) for i, img in enumerate(images) if i%2 == 0], duration=35)

KeyboardInterrupt: 

# PPO for Image Classification on MNIST

In [48]:
from tensorflow import keras
from tensorflow.keras import layers
import tensorflow as tf
from stable_baselines3.common.vec_env.dummy_vec_env import DummyVecEnv
from stable_baselines3.common import logger
from stable_baselines3.common.monitor import Monitor
import time
import gym
import random
#from stable_baselines3 import bench


In [49]:
# Model / data parameters
num_classes = 10
input_shape = (28, 28, 1)

# the data, split between train and test sets
(x_train, y_train), (x_test, y_test) = keras.datasets.mnist.load_data()

# Scale images to the [0, 1] range
x_train = x_train.astype("float32") / 255
x_test = x_test.astype("float32") / 255
# Make sure images have shape (28, 28, 1)
x_train = np.expand_dims(x_train, -1)
x_test = np.expand_dims(x_test, -1)
print("x_train shape:", x_train.shape)
print(x_train.shape[0], "train samples")
print(x_test.shape[0], "test samples")


# convert class vectors to binary class matrices
y_train_one_hot = keras.utils.to_categorical(y_train, num_classes)
y_test_one_hot = keras.utils.to_categorical(y_test, num_classes)

x_train shape: (60000, 28, 28, 1)
60000 train samples
10000 test samples


In [50]:

class MnistEnv(gym.Env):
    def __init__(self, images_per_episode=1, dataset=(x_train, y_train), random=True):
        super().__init__()

        self.action_space = gym.spaces.Discrete(10)
        self.observation_space = gym.spaces.Box(low=0, high=1,
                                                shape=(28, 28, 1),
                                                dtype=np.float32)

        self.images_per_episode = images_per_episode
        self.step_count = 0

        self.x, self.y = dataset
        self.random = random
        self.dataset_idx = 0

    def step(self, action):
        done = False
        reward = int(action == self.expected_action)

        obs = self._next_obs()

        self.step_count += 1
        if self.step_count >= self.images_per_episode:
            done = True

        return obs, reward, done, {}

    def reset(self):
        self.step_count = 0

        obs = self._next_obs()
        return obs

    def _next_obs(self):
        if self.random:
            next_obs_idx = random.randint(0, len(self.x) - 1)
            self.expected_action = int(self.y[next_obs_idx])
            obs = self.x[next_obs_idx]

        else:
            obs = self.x[self.dataset_idx]
            self.expected_action = int(self.y[self.dataset_idx])

            self.dataset_idx += 1
            if self.dataset_idx >= len(self.x):
                raise StopIteration()

        return obs


In [51]:
def mnist_ppo():
    logger.configure('./logs/mnist_ppo', ['stdout', 'tensorboard'])
    env = DummyVecEnv([lambda: Monitor(MnistEnv(images_per_episode=1), './logs/mnist_ppo')])

    model = PPO(
        policy='MlpPolicy',
        env=env,
        n_steps=32,
        batch_size=64,
        n_epochs=10,
        learning_rate=0.0001,
        ent_coef=0.01,
        gamma=0.99,
        gae_lambda=0.95,
        clip_range=0.2,
        clip_range_vf=None,
        vf_coef=0.5,
        max_grad_norm=0.5,
        target_kl=None,
        tensorboard_log="./logs/mnist_ppo",
        verbose=1,
    )
    
    model.learn(total_timesteps=int(1.2e5))
    return model

start_time = time.time()
ppo_model = mnist_ppo()
print("PPO Training Time:", time.time() - start_time)

Logging to ./logs/mnist_ppo
Using cpu device
Logging to ./logs/mnist_ppo/PPO_1
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | 0.125    |
| time/              |          |
|    fps             | 1255     |
|    iterations      | 1        |
|    time_elapsed    | 0        |
|    total_timesteps | 32       |
---------------------------------
-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1             |
|    ep_rew_mean          | 0.0938        |
| time/                   |               |
|    fps                  | 797           |
|    iterations           | 2             |
|    time_elapsed         | 0             |
|    total_timesteps      | 64            |
| train/                  |               |
|    approx_kl            | 9.3786046e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entr

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1             |
|    ep_rew_mean          | 0.11          |
| time/                   |               |
|    fps                  | 618           |
|    iterations           | 11            |
|    time_elapsed         | 0             |
|    total_timesteps      | 352           |
| train/                  |               |
|    approx_kl            | 0.00011197105 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -2.3          |
|    explained_variance   | -0.345        |
|    learning_rate        | 0.0001        |
|    loss                 | 0.037         |
|    n_updates            | 100           |
|    policy_gradient_loss | -0.00377      |
|    value_loss           | 0.163         |
-------------------------------------------
-------------------------------------------
| rollout/                |     

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1             |
|    ep_rew_mean          | 0.12          |
| time/                   |               |
|    fps                  | 607           |
|    iterations           | 20            |
|    time_elapsed         | 1             |
|    total_timesteps      | 640           |
| train/                  |               |
|    approx_kl            | 0.00020501763 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -2.3          |
|    explained_variance   | -0.0964       |
|    learning_rate        | 0.0001        |
|    loss                 | 0.016         |
|    n_updates            | 190           |
|    policy_gradient_loss | -0.00568      |
|    value_loss           | 0.128         |
-------------------------------------------
-------------------------------------------
| rollout/                |     

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1            |
|    ep_rew_mean          | 0.18         |
| time/                   |              |
|    fps                  | 598          |
|    iterations           | 29           |
|    time_elapsed         | 1            |
|    total_timesteps      | 928          |
| train/                  |              |
|    approx_kl            | 9.467453e-05 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -2.3         |
|    explained_variance   | -0.169       |
|    learning_rate        | 0.0001       |
|    loss                 | 0.0376       |
|    n_updates            | 280          |
|    policy_gradient_loss | -0.00464     |
|    value_loss           | 0.176        |
------------------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1            |
|    ep_rew_mean          | 0.1          |
| time/                   |              |
|    fps                  | 573          |
|    iterations           | 38           |
|    time_elapsed         | 2            |
|    total_timesteps      | 1216         |
| train/                  |              |
|    approx_kl            | 0.0005669128 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -2.29        |
|    explained_variance   | -0.138       |
|    learning_rate        | 0.0001       |
|    loss                 | 0.0216       |
|    n_updates            | 370          |
|    policy_gradient_loss | -0.00713     |
|    value_loss           | 0.141        |
------------------------------------------
-------------------------------------------
| rollout/                |               |
|    ep_l

...

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1            |
|    ep_rew_mean          | 0.93         |
| time/                   |              |
|    fps                  | 574          |
|    iterations           | 3706         |
|    time_elapsed         | 206          |
|    total_timesteps      | 118592       |
| train/                  |              |
|    approx_kl            | 0.0070642848 |
|    clip_fraction        | 0.0219       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.0796      |
|    explained_variance   | -0.136       |
|    learning_rate        | 0.0001       |
|    loss                 | -0.0227      |
|    n_updates            | 37050        |
|    policy_gradient_loss | -0.0153      |
|    value_loss           | 0.0361       |
------------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_m

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1           |
|    ep_rew_mean          | 0.91        |
| time/                   |             |
|    fps                  | 574         |
|    iterations           | 3716        |
|    time_elapsed         | 206         |
|    total_timesteps      | 118912      |
| train/                  |             |
|    approx_kl            | 0.019627443 |
|    clip_fraction        | 0.0563      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.179      |
|    explained_variance   | 0.174       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.0178     |
|    n_updates            | 37150       |
|    policy_gradient_loss | -0.0401     |
|    value_loss           | 0.116       |
-----------------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1   

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1           |
|    ep_rew_mean          | 0.95        |
| time/                   |             |
|    fps                  | 575         |
|    iterations           | 3726        |
|    time_elapsed         | 207         |
|    total_timesteps      | 119232      |
| train/                  |             |
|    approx_kl            | 0.004236318 |
|    clip_fraction        | 0.0156      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.117      |
|    explained_variance   | -0.225      |
|    learning_rate        | 0.0001      |
|    loss                 | -0.0266     |
|    n_updates            | 37250       |
|    policy_gradient_loss | -0.02       |
|    value_loss           | 0.0357      |
-----------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1     

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1            |
|    ep_rew_mean          | 0.96         |
| time/                   |              |
|    fps                  | 575          |
|    iterations           | 3736         |
|    time_elapsed         | 207          |
|    total_timesteps      | 119552       |
| train/                  |              |
|    approx_kl            | 0.0127132125 |
|    clip_fraction        | 0.0219       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.0518      |
|    explained_variance   | -0.246       |
|    learning_rate        | 0.0001       |
|    loss                 | -0.0155      |
|    n_updates            | 37350        |
|    policy_gradient_loss | -0.0268      |
|    value_loss           | 0.0378       |
------------------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1            |
|    ep_rew_mean          | 0.92         |
| time/                   |              |
|    fps                  | 575          |
|    iterations           | 3746         |
|    time_elapsed         | 208          |
|    total_timesteps      | 119872       |
| train/                  |              |
|    approx_kl            | 0.0134210475 |
|    clip_fraction        | 0.0406       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.0918      |
|    explained_variance   | -0.00462     |
|    learning_rate        | 0.0001       |
|    loss                 | -0.0229      |
|    n_updates            | 37450        |
|    policy_gradient_loss | -0.0346      |
|    value_loss           | 0.0601       |
------------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_m

In [56]:
def mnist_ppo_eval(ppo_model):
    attempts, correct = 0,0

    env = DummyVecEnv([lambda: MnistEnv(images_per_episode=1, dataset=(x_test, y_test), random=False)])
    
    try:
        while True:
            obs, done = env.reset(), [False]
            while not done[0]:
                obs, rew, done, _ = env.step(ppo_model.predict(obs)[0])

                attempts += 1
                if rew[0] > 0:
                    correct += 1
    except StopIteration:
        print()
        print('validation done...')
        print('Accuracy: {0}%'.format((float(correct) / attempts) * 100))

mnist_ppo_eval(ppo_model)


validation done...
Accuracy: 92.85928592859285%


# Running Q-Learning on MNIST

In [84]:
def mnist_QL():
    logger.configure('./logs/mnist_ql', ['stdout', 'tensorboard'])
    env = DummyVecEnv([lambda: Monitor(MnistEnv(images_per_episode=1), './logs/mnist_ql')])
    Q = np.zeros([28*28, 10])
    alpha = .1
    G = 0
    for episode in range(1,1000000):
        done = False
        G, reward = 0,0
        state = env.reset()
        while done != True:
                if random.random() < (10 / (episode*.1)):  # take less random steps as you learn more about the game
                    action = random.randint(0,env.action_space.n-1)
                else:
                    action = np.argmax(Q[state])
                state2, reward, done, info = env.step([action])  # 2
                Q[state, action] += alpha * (reward + np.max(Q[state2]) - Q[state, action])
                G += reward
                state = state2
    return Q

start_time = time.time()
ql_model = mnist_QL()
print("Q-Learning Training Time:", time.time() - start_time)


Logging to ./logs/mnist_ql
Q-Learning Training Time: 173.64713215827942


In [87]:
def mnist_QL_eval(ql_model):
    attempts, correct = 0,0

    env = DummyVecEnv([lambda: MnistEnv(images_per_episode=1, dataset=(x_test, y_test), random=False)])
    
    try:
        while True:
            obs, done = env.reset(), [False]
            while not done[0]:
                action = np.argmax(ql_model[obs[:,:,0].ravel().astype(int)])
                obs, rew, done, _ = env.step([action])  # wrap action in an array

                attempts += 1
                if rew[0] > 0:
                    correct += 1
    except StopIteration:
        print()
        print('validation done...')
        print('Accuracy: {0}%'.format((float(correct) / attempts) * 100))

mnist_QL_eval(ql_model)



validation done...
Accuracy: 9.63096309630963%
